# Compute Error


## Robot setup

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import time
from sklearn.utils.extmath import cartesian
import transforms3d as t3d

import sys
sys.path.append("..")
sys.path.append("../../")

from armControl import *
from forwardKinematics import robot_config
from utils.motor_setup import maxonGearSmall
import armControl

from utils.NatNetClient2 import NatNetClient
from utils.GetJointData import data, NatNetFuncs #receiveNewFrame, receiveRigidBodyFrameList

import signal

import matplotlib.pyplot as plt

socket_ip = '192.168.0.110'
socket_port = 1125

server_ip = "192.168.0.105"
multicastAddress = "239.255.42.99"

joint_names = ['Base','RigidBody']
ids = [0, 1]

#trajPlanner = trajectoryGenerator()

motors = maxonGearSmall()
motors.tcp_init(socket_ip, socket_port)

#axis_motor_indexes = np.array([-1, -1, -1, 0, 3, 2, 1]) #indexed from 0 for motors and axis
#velocity = np.ones(8)*3.14/20


## Command motors w/ indexing for joints

def commandJoints(setpoint_arm, trajectory = True):
    myArm = armControl.remoteRobotArm()
    myArm.jointAngleSetpoint = setpoint_arm
    myArm.updateMotorArmMixing()
    setpoint_motor = np.zeros(8)
    setpoint_motor[axis_motor_indexes[3:7]] = myArm.motorAngleSetpoint[3:7]
    if trajectory:
        motors.run_trajectory(setpoint_motor, velocity)
    else:
        motors.command_motors_radians(setpoint_motor)


## Arm Motors

In [248]:
print("Arming motors now...")
motors.arm_motors()


Arming motors now...
We had a timeout (probably)?
initializing motors to [     -1   43938  -43975 -205129       0       0       0       0]
We had a timeout (probably)?
Arming motors


## Manual motor zeroing

In [ ]:
from importlib import reload
reload(armControl)

myArm = armControl.remoteRobotArm()

setpoint_arm = np.array([0.0,0.0,-0.,0,0.0,0,0])
myArm.commandJoints(motors, setpoint_arm)
time.sleep(0.5)


In [ ]:
for i in range(8):
    motors.zero_motors_radians(i, motors.get_motors_position_radians()[i])

## Test arm joint mixing

### this is old, now in "commandJoints" above

import armControl
from importlib import reload
reload(armControl)

setpoint_arm = np.array([0,0,0,0,0,0,-0])
myArm = armControl.remoteRobotArm()
myArm.jointAngleSetpoint = setpoint_arm
myArm.updateMotorArmMixing()
print(myArm.motorAngleSetpoint)

setpoint_motor = np.zeros(8)
setpoint_motor[axis_motor_indexes[3:7]] = myArm.motorAngleSetpoint[3:7]
print(setpoint_motor)
motors.run_trajectory(setpoint_motor, velocity)


In [247]:
print(myArm.jointUpperLimits)
print(myArm.jointLowerLimits)
joint7_angles = np.linspace(myArm.jointLowerLimits[-1],myArm.jointUpperLimits[-1], num=50)
joint6_angles = np.linspace(myArm.jointLowerLimits[-2],myArm.jointUpperLimits[-2], num=500)
joint5_angles = np.linspace(myArm.jointLowerLimits[-3],myArm.jointUpperLimits[-3], num=50)
joint4_angles = np.linspace(myArm.jointLowerLimits[-4],myArm.jointUpperLimits[-4], num=50)

joint_angles = [np.array(joint7_angles), np.array(joint6_angles), np.array(joint5_angles), np.array(joint4_angles)]
PointsMatrix = cartesian(joint_angles)
num_sweeps = 3
num_points = len(PointsMatrix[:,1])
Pos_Points = np.zeros(shape = (num_points, 3, num_sweeps))
Quat_Points = np.zeros(shape = (num_points, 4, num_sweeps))

for i in range(num_sweeps):
    for j in range(len(PointsMatrix[:,1])):
        setpoint_base = np.array([0,0,0])
        setpoint_arm = np.array(PointsMatrix[j,:])
        setpoint_robot = np.append(setpoint_base, setpoint_arm)
        myArm.commandJoints(motors, setpoint_robot, trajectory = True)
        time.sleep(5)
        myArm.commandJoints(motors, setpoint_robot, trajectory = False)
        time.sleep(0.02)
        
        track_data.parse_data(NatNet.joint_data, NatNet.frame) #updates the frame and data that is being used
        
        #add in optitrack position measurements
        time.sleep(5)
        base = track_data.bodies[0].homogenous_mat
        base_inv = track_data.bodies[0].homg_inv
        needle = track_data.bodies[1].homogenous_mat
        needle_base, needlebase_pos, needlebase_euler, _ = track_data.homg_mat_mult(base_inv,needle)
        needlebase_rot = np.array(needle_base[0:3,0:3])
        needlebase_quat = t3d.quaternions.mat2quat(needlebase_rot)
        Pos_Points[j,:,i] = np.array(needlebase_pos)
        Quat_Points[j,:,i] = np.array(needlebase_quat)
    

[8.20e+01 4.20e+01 1.75e+00 8.72e-01 8.72e-01 8.72e-01 4.75e-02]
[-82.    -42.     -1.75   -0.872  -0.872  -0.872   0.   ]
list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, jo

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be

...

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***



*** C side has an error or needs to be armed ***

list index: 0, joint_data: (0.1906207948923111, -0.7672795057296753, -0.1409233808517456)
list index: 1, joint_data: (0.09696192294359207, -0.7160965204238892, -0.1645631641149521)
*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an e

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***



*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***

*** C side has an error or needs to be armed ***



KeyboardInterrupt: 

In [ ]:
#Compute Avg of Positions (x,y,z)
Pos_Avg = np.zeros(shape = (1, 3, num_sweeps))
for i in range(num_sweeps):
    Pos_Avg(1,:,i) = np.mean(Pos_Points, axis=0)
Pos_Error = np.zeros(shape = (num_points, 3, num_sweeps))
sweepNum = np.linspace(1,num_sweeps,num_sweeps)

#Compute Error of Positions (x,y,z)
for j in range(num_sweeps):
    for k in range(num_points):
        Pos_Error = Pos_Points[k,:,j] - Pos_Avg[1,:,j]
    print("Sweep {} Position Error: {}".format(sweepNum[j], Pos_Error[:,:,j]))




## Sine wave / profile test

In [ ]:
dt = 0.005
runtime = 10
num_elements = int(runtime/dt)
setpoints = np.zeros((num_elements, 7))
frequency = 0.1
amplitude = np.pi/6
for i in range(num_elements):
    setpoints[i,:] = (np.ones(7) * np.sin(i*dt*2*pi*frequency)*amplitude)


start_time = time.time()

currents_mA = []
for i in range(num_elements):
    current_time = time.time()
    setpoint = setpoints[i]
    myArm.commandJoints(motors, setpoint, trajectory=False)
    time.sleep(dt)

time.sleep(1.5)

motors.run_trajectory(np.zeros(8), velocity)


## Cleanup

In [134]:
setpoints = np.zeros(8)
velocity = np.ones(8)*3.14/5
motors.run_trajectory(setpoints, velocity)
time.sleep(20)
motors.tcp_close()

In [120]:
motors.tcp_close()